# Caffe 算子测试

In [1]:
%cd ../..
import set_env

/media/pc/data/lxw/ai/tvm-book/doc/topics


In [2]:
import os
import logging
import numpy as np

from google.protobuf import text_format
import caffe
from caffe import layers as L, params as P
from caffe.proto import caffe_pb2 as pb

import tvm
import tvm.testing
from tvm import relay
from tvm.contrib import graph_executor
from tvm.contrib.download import download_testdata
os.environ["GLOG_minloglevel"] = "2"

logging.basicConfig(level=logging.ERROR)

def save_prototxt(n_netspec, f_path):
    """Generate .prototxt file according to caffe.NetSpec"""
    s = n_netspec.to_proto()
    with open(f_path, "w") as f:
        f.write(str(s))


def save_solver(solver_file, proto_file, blob_file):
    """Define a solver proto, you can change the configs."""
    blob_file_prefix = blob_file.split(".caffemodel")[0]
    s = pb.SolverParameter()
    s.train_net = proto_file
    s.base_lr = 0.01
    s.momentum = 0.9
    s.weight_decay = 0.0005
    s.lr_policy = "inv"
    s.gamma = 0.0001
    s.power = 0.75
    s.display = 1
    s.max_iter = 100000
    s.snapshot = 100000
    s.snapshot_prefix = blob_file_prefix

    with open(solver_file, "w") as f:
        f.write(str(s))


def save_caffemodel(solver_file, blob_file):
    """Generate .caffemodel file."""
    solver = caffe.SGDSolver(solver_file)
    solver.net.save(blob_file)

def gen_model_files(n_netspec, proto_file, blob_file, solver_file):
    save_prototxt(n_netspec, proto_file)
    save_solver(solver_file, proto_file, blob_file)
    save_caffemodel(solver_file, blob_file)

def run_caffe(data, proto_file, blob_file):
    """Run caffe model by Caffe according to .caffemodel and .prototxt"""
    net = caffe.Net(proto_file, blob_file, caffe.TEST)
    if isinstance(data, (list, tuple)):
        for idx, d in enumerate(data):
            net.blobs["data" + str(idx)].data[...] = d
    else:
        net.blobs["data"].data[...] = data
    out = net.forward()

    caffe_output = []
    for i in range(len(out.keys())):
        if "output" + str(i) not in out.keys():
            caffe_output.clear()
            return list(out.values())
        caffe_output.append(out["output" + str(i)])
    return caffe_output

In [3]:
def siso_op(shape, func, *args, **kwargs):
    """Create single input and single output Caffe op"""
    n = caffe.NetSpec()
    n.data = L.Input(input_param={"shape": {"dim": list(shape)}})
    n.output = func(n.data, *args, **kwargs)
    return n

def miso_op(shapes, func, *args, **kwargs):
    """Create multi input and single output Caffe op"""
    n = caffe.NetSpec()
    if not isinstance(shapes, (tuple, list)):
        raise TypeError(f"Need tuple or list but get {type(shapes)}")
    input_list = []
    for idx, shape in enumerate(shapes):
        n["data" + str(idx)] = L.Input(input_param={"shape": {"dim": list(shape)}})
        input_list.append(n["data" + str(idx)])
    n.output = func(*input_list, *args, **kwargs)
    return n


def simo_op(shape, func, *args, **kwargs):
    """Create single input and multi output Caffe op"""
    n = caffe.NetSpec()
    n.data = L.Input(input_param={"shape": {"dim": list(shape)}})
    output_list = func(n.data, *args, **kwargs)
    for idx, out in enumerate(output_list):
        n["output" + str(idx)] = out
    return n

In [4]:
def creat_op(shapes, func_op, **kwargs):
    shape_list = []
    if isinstance(shapes, (list, tuple)):
        n = miso_op(shapes, func_op, **kwargs)
        for shape in shapes:
            shape_list.extend(list(shape))
    else:
        output_num = 1
        if "ntop" in kwargs:
            output_num = kwargs["ntop"]
        if output_num == 1:
            n = siso_op(shapes, func_op, **kwargs)
        else:
            n = simo_op(shapes, func_op, **kwargs)
        shape_list = list(shapes)
    return n, shape_list

## caffe BatchNorm

In [5]:
op_name = "BatchNorm"
root_dir = "./.temp"
proto_file = f"{root_dir}/{op_name}.prototxt"
blob_file = f"{root_dir}/{op_name}.caffemodel"
solver_file = f"{root_dir}/{op_name}_solver.prototxt"
shape = (1, 3, 10, 10)
n_netspec = siso_op(shape, L.BatchNorm, moving_average_fraction=0.999, eps=1e-5)
# obtain the .caffemodel file and .prototxt file
gen_model_files(n_netspec, proto_file, blob_file, solver_file)
# run model in Caffe
data = np.random.rand(*shape).astype(np.float32)
caffe_out = run_caffe(data, proto_file, blob_file)

I0914 09:12:10.797545 1956768 solver.cpp:45] Initializing solver from parameters: 
train_net: "./.temp/BatchNorm.prototxt"
base_lr: 0.01
display: 1
max_iter: 100000
lr_policy: "inv"
gamma: 0.0001
power: 0.75
momentum: 0.9
weight_decay: 0.0005
snapshot: 100000
snapshot_prefix: "./.temp/BatchNorm"
I0914 09:12:10.797695 1956768 solver.cpp:92] Creating training net from train_net file: ./.temp/BatchNorm.prototxt
I0914 09:12:10.798242 1956768 net.cpp:53] Initializing net from parameters: 
state {
  phase: TRAIN
}
layer {
  name: "data"
  type: "Input"
  top: "data"
  input_param {
    shape {
      dim: 1
      dim: 3
      dim: 10
      dim: 10
    }
  }
}
layer {
  name: "output"
  type: "BatchNorm"
  bottom: "data"
  top: "output"
  batch_norm_param {
    moving_average_fraction: 0.999
    eps: 1e-05
  }
}
I0914 09:12:10.798317 1956768 layer_factory.hpp:77] Creating layer data
I0914 09:12:10.798336 1956768 net.cpp:86] Creating Layer data
I0914 09:12:10.798341 1956768 net.cpp:382] data ->

In [6]:
init_net = pb.NetParameter()
predict_net = pb.NetParameter()
# load model
with open(proto_file, "r") as f:
    text_format.Merge(f.read(), predict_net)
# load blob
with open(blob_file, "rb") as f:
    init_net.ParseFromString(f.read())
shape_dict = {"data": shape}
dtype_dict = {"data": "float32"}
mod, params = relay.frontend.from_caffe(init_net, predict_net, shape_dict, dtype_dict)
with tvm.transform.PassContext(opt_level=3):
    mod = relay.quantize.prerequisite_optimize(mod, params)
mod.show()

## caffe concat

In [7]:
np.random.rand(), np.random.rand(1, 2, 10, 10)

(0.5722476838666538,
 array([[[[0.61123624, 0.37588209, 0.02169732, 0.18100491, 0.95849767,
           0.02395107, 0.20080887, 0.33766822, 0.11885211, 0.86539518],
          [0.10359814, 0.3886911 , 0.65470521, 0.05712175, 0.71074179,
           0.42249166, 0.37142238, 0.65421255, 0.99183236, 0.9922702 ],
          [0.11899492, 0.46457062, 0.89906396, 0.33470963, 0.48111082,
           0.86251228, 0.52144183, 0.91341972, 0.77010121, 0.49809878],
          [0.89288594, 0.59797711, 0.41111909, 0.37215822, 0.82308275,
           0.43773541, 0.48900654, 0.09655104, 0.6752475 , 0.73714895],
          [0.94505647, 0.751491  , 0.79973422, 0.49016049, 0.98444054,
           0.74379714, 0.10746913, 0.25731962, 0.25730886, 0.74203572],
          [0.31960305, 0.73112817, 0.87677291, 0.15800022, 0.80400933,
           0.44788138, 0.9895867 , 0.42715959, 0.71428694, 0.16113941],
          [0.1914514 , 0.75825183, 0.50116843, 0.65810231, 0.75718552,
           0.53124754, 0.4343793 , 0.32263688, 0.6

In [8]:
def _test_concat(shape_list, axis=1, op_name="concat",):
    proto_file = f"{root_dir}/{op_name}.prototxt"
    blob_file = f"{root_dir}/{op_name}.caffemodel"
    solver_file = f"{root_dir}/{op_name}_solver.prototxt"
    n_netspec = miso_op(shape_list, L.Concat, axis=axis)
    # obtain the .caffemodel file and .prototxt file
    gen_model_files(n_netspec, proto_file, blob_file, solver_file)
    # run model in Caffe
    data = [np.random.rand(*shape).astype(np.float32) for shape in shape_list]
    caffe_out = run_caffe(data, proto_file, blob_file)
    init_net = pb.NetParameter()
    predict_net = pb.NetParameter()
    # load model
    with open(proto_file, "r") as f:
        text_format.Merge(f.read(), predict_net)
    # load blob
    with open(blob_file, "rb") as f:
        init_net.ParseFromString(f.read())
    shape_dict = [{f"data_{k}": shape} for k, shape in enumerate(shape_list)]
    dtype_dict = [{f"data_{k}": "float32"} for k, shape in enumerate(shape_list)]
    mod, params = relay.frontend.from_caffe(init_net, predict_net, shape_dict, dtype_dict)
    return mod, params

In [9]:
mod, params = _test_concat([(1, 3, 10, 10), (1, 2, 10, 10)], axis=1)

I0914 09:12:11.276784 1956768 solver.cpp:45] Initializing solver from parameters: 
train_net: "./.temp/concat.prototxt"
base_lr: 0.01
display: 1
max_iter: 100000
lr_policy: "inv"
gamma: 0.0001
power: 0.75
momentum: 0.9
weight_decay: 0.0005
snapshot: 100000
snapshot_prefix: "./.temp/concat"
I0914 09:12:11.276893 1956768 solver.cpp:92] Creating training net from train_net file: ./.temp/concat.prototxt
I0914 09:12:11.276965 1956768 net.cpp:53] Initializing net from parameters: 
state {
  phase: TRAIN
}
layer {
  name: "data0"
  type: "Input"
  top: "data0"
  input_param {
    shape {
      dim: 1
      dim: 3
      dim: 10
      dim: 10
    }
  }
}
layer {
  name: "data1"
  type: "Input"
  top: "data1"
  input_param {
    shape {
      dim: 1
      dim: 2
      dim: 10
      dim: 10
    }
  }
}
layer {
  name: "output"
  type: "Concat"
  bottom: "data0"
  bottom: "data1"
  top: "output"
  concat_param {
    axis: 1
  }
}
I0914 09:12:11.277004 1956768 layer_factory.hpp:77] Creating layer d

In [10]:
mod.show()

In [11]:
mod, params = _test_concat([(3, 10, 10), (2, 10, 10)], axis=0)

I0914 09:12:11.297618 1956768 solver.cpp:45] Initializing solver from parameters: 
train_net: "./.temp/concat.prototxt"
base_lr: 0.01
display: 1
max_iter: 100000
lr_policy: "inv"
gamma: 0.0001
power: 0.75
momentum: 0.9
weight_decay: 0.0005
snapshot: 100000
snapshot_prefix: "./.temp/concat"
I0914 09:12:11.297690 1956768 solver.cpp:92] Creating training net from train_net file: ./.temp/concat.prototxt
I0914 09:12:11.297744 1956768 net.cpp:53] Initializing net from parameters: 
state {
  phase: TRAIN
}
layer {
  name: "data0"
  type: "Input"
  top: "data0"
  input_param {
    shape {
      dim: 3
      dim: 10
      dim: 10
    }
  }
}
layer {
  name: "data1"
  type: "Input"
  top: "data1"
  input_param {
    shape {
      dim: 2
      dim: 10
      dim: 10
    }
  }
}
layer {
  name: "output"
  type: "Concat"
  bottom: "data0"
  bottom: "data1"
  top: "output"
  concat_param {
    axis: 0
  }
}
I0914 09:12:11.297775 1956768 layer_factory.hpp:77] Creating layer data0
I0914 09:12:11.297782

In [12]:
mod.show()

## caffe Convolution

In [13]:
def _test_conv2d(shape_list,  op_name="conv2d", **kwargs):
    proto_file = f"{root_dir}/{op_name}.prototxt"
    blob_file = f"{root_dir}/{op_name}.caffemodel"
    solver_file = f"{root_dir}/{op_name}_solver.prototxt"
    n_netspec = miso_op(shape_list, L.Convolution, **kwargs)
    # obtain the .caffemodel file and .prototxt file
    gen_model_files(n_netspec, proto_file, blob_file, solver_file)
    # run model in Caffe
    data = [np.random.rand(*shape).astype(np.float32) for shape in shape_list]
    caffe_out = run_caffe(data, proto_file, blob_file)
    init_net = pb.NetParameter()
    predict_net = pb.NetParameter()
    # load model
    with open(proto_file, "r") as f:
        text_format.Merge(f.read(), predict_net)
    # load blob
    with open(blob_file, "rb") as f:
        init_net.ParseFromString(f.read())
    shape_dict = [{f"data_{k}": shape} for k, shape in enumerate(shape_list)]
    dtype_dict = [{f"data_{k}": "float32"} for k, _ in enumerate(shape_list)]
    mod, params = relay.frontend.from_caffe(init_net, predict_net, shape_dict, dtype_dict)
    return mod, params

In [14]:
shape_list = [(1, 3, 10, 10)]
mod, params = _test_conv2d(
    shape_list,
    num_output=20,
    bias_term=True,
    pad=0,
    kernel_size=3,
    stride=2,
    dilation=1,
    weight_filler=dict(type="xavier"),
    bias_filler=dict(type="xavier"),
)

I0914 09:12:11.327899 1956768 solver.cpp:45] Initializing solver from parameters: 
train_net: "./.temp/conv2d.prototxt"
base_lr: 0.01
display: 1
max_iter: 100000
lr_policy: "inv"
gamma: 0.0001
power: 0.75
momentum: 0.9
weight_decay: 0.0005
snapshot: 100000
snapshot_prefix: "./.temp/conv2d"
I0914 09:12:11.327972 1956768 solver.cpp:92] Creating training net from train_net file: ./.temp/conv2d.prototxt
I0914 09:12:11.328034 1956768 net.cpp:53] Initializing net from parameters: 
state {
  phase: TRAIN
}
layer {
  name: "data0"
  type: "Input"
  top: "data0"
  input_param {
    shape {
      dim: 1
      dim: 3
      dim: 10
      dim: 10
    }
  }
}
layer {
  name: "output"
  type: "Convolution"
  bottom: "data0"
  top: "output"
  convolution_param {
    num_output: 20
    bias_term: true
    pad: 0
    kernel_size: 3
    stride: 2
    weight_filler {
      type: "xavier"
    }
    bias_filler {
      type: "xavier"
    }
    dilation: 1
  }
}
I0914 09:12:11.328068 1956768 layer_factory.hp

In [15]:
mod.show()

In [16]:
mod, params = _test_conv2d(
    shape_list,
    num_output=20,
    bias_term=False,
    pad=[1, 2],
    kernel_size=3,
    stride=2,
    dilation=1,
    weight_filler=dict(type="xavier"),
    bias_filler=dict(type="xavier"),
)

I0914 09:12:11.350931 1956768 solver.cpp:45] Initializing solver from parameters: 
train_net: "./.temp/conv2d.prototxt"
base_lr: 0.01
display: 1
max_iter: 100000
lr_policy: "inv"
gamma: 0.0001
power: 0.75
momentum: 0.9
weight_decay: 0.0005
snapshot: 100000
snapshot_prefix: "./.temp/conv2d"
I0914 09:12:11.351027 1956768 solver.cpp:92] Creating training net from train_net file: ./.temp/conv2d.prototxt
I0914 09:12:11.351083 1956768 net.cpp:53] Initializing net from parameters: 
state {
  phase: TRAIN
}
layer {
  name: "data0"
  type: "Input"
  top: "data0"
  input_param {
    shape {
      dim: 1
      dim: 3
      dim: 10
      dim: 10
    }
  }
}
layer {
  name: "output"
  type: "Convolution"
  bottom: "data0"
  top: "output"
  convolution_param {
    num_output: 20
    bias_term: false
    pad: 1
    pad: 2
    kernel_size: 3
    stride: 2
    weight_filler {
      type: "xavier"
    }
    bias_filler {
      type: "xavier"
    }
    dilation: 1
  }
}
I0914 09:12:11.351116 1956768 laye

In [17]:
mod.show()

In [18]:
mod, params = _test_conv2d(
    shape_list,
    num_output=20,
    bias_term=True,
    pad=[1, 2],
    kernel_size=[3, 5],
    stride=[2, 1],
    dilation=[1, 2],
    weight_filler=dict(type="xavier"),
    bias_filler=dict(type="xavier"),
)

I0914 09:12:11.373440 1956768 solver.cpp:45] Initializing solver from parameters: 
train_net: "./.temp/conv2d.prototxt"
base_lr: 0.01
display: 1
max_iter: 100000
lr_policy: "inv"
gamma: 0.0001
power: 0.75
momentum: 0.9
weight_decay: 0.0005
snapshot: 100000
snapshot_prefix: "./.temp/conv2d"
I0914 09:12:11.373510 1956768 solver.cpp:92] Creating training net from train_net file: ./.temp/conv2d.prototxt
I0914 09:12:11.373567 1956768 net.cpp:53] Initializing net from parameters: 
state {
  phase: TRAIN
}
layer {
  name: "data0"
  type: "Input"
  top: "data0"
  input_param {
    shape {
      dim: 1
      dim: 3
      dim: 10
      dim: 10
    }
  }
}
layer {
  name: "output"
  type: "Convolution"
  bottom: "data0"
  top: "output"
  convolution_param {
    num_output: 20
    bias_term: true
    pad: 1
    pad: 2
    kernel_size: 3
    kernel_size: 5
    stride: 2
    stride: 1
    weight_filler {
      type: "xavier"
    }
    bias_filler {
      type: "xavier"
    }
    dilation: 1
    dila

In [19]:
mod.show()

In [20]:
mod, params = _test_conv2d(
    shape_list,
    num_output=20,
    bias_term=True,
    pad_h=1,
    pad_w=2,
    kernel_h=3,
    kernel_w=5,
    stride_h=2,
    stride_w=1,
    dilation=[1, 2],
    weight_filler=dict(type="xavier"),
    bias_filler=dict(type="xavier"),
)

I0914 09:12:11.396004 1956768 solver.cpp:45] Initializing solver from parameters: 
train_net: "./.temp/conv2d.prototxt"
base_lr: 0.01
display: 1
max_iter: 100000
lr_policy: "inv"
gamma: 0.0001
power: 0.75
momentum: 0.9
weight_decay: 0.0005
snapshot: 100000
snapshot_prefix: "./.temp/conv2d"
I0914 09:12:11.396075 1956768 solver.cpp:92] Creating training net from train_net file: ./.temp/conv2d.prototxt
I0914 09:12:11.396133 1956768 net.cpp:53] Initializing net from parameters: 
state {
  phase: TRAIN
}
layer {
  name: "data0"
  type: "Input"
  top: "data0"
  input_param {
    shape {
      dim: 1
      dim: 3
      dim: 10
      dim: 10
    }
  }
}
layer {
  name: "output"
  type: "Convolution"
  bottom: "data0"
  top: "output"
  convolution_param {
    num_output: 20
    bias_term: true
    weight_filler {
      type: "xavier"
    }
    bias_filler {
      type: "xavier"
    }
    pad_h: 1
    pad_w: 2
    kernel_h: 3
    kernel_w: 5
    stride_h: 2
    stride_w: 1
    dilation: 1
    di

In [21]:
mod.show()

In [22]:
mod, params = _test_conv2d(
    [(1, 2, 10, 10)],
    num_output=20,
    bias_term=True,
    pad=[1, 2],
    kernel_size=[3, 5],
    stride=[2, 1],
    dilation=[1, 2],
    weight_filler=dict(type="xavier"),
    bias_filler=dict(type="xavier"),
    group=2,
)

I0914 09:12:11.421512 1956768 solver.cpp:45] Initializing solver from parameters: 
train_net: "./.temp/conv2d.prototxt"
base_lr: 0.01
display: 1
max_iter: 100000
lr_policy: "inv"
gamma: 0.0001
power: 0.75
momentum: 0.9
weight_decay: 0.0005
snapshot: 100000
snapshot_prefix: "./.temp/conv2d"
I0914 09:12:11.421586 1956768 solver.cpp:92] Creating training net from train_net file: ./.temp/conv2d.prototxt
I0914 09:12:11.421649 1956768 net.cpp:53] Initializing net from parameters: 
state {
  phase: TRAIN
}
layer {
  name: "data0"
  type: "Input"
  top: "data0"
  input_param {
    shape {
      dim: 1
      dim: 2
      dim: 10
      dim: 10
    }
  }
}
layer {
  name: "output"
  type: "Convolution"
  bottom: "data0"
  top: "output"
  convolution_param {
    num_output: 20
    bias_term: true
    pad: 1
    pad: 2
    kernel_size: 3
    kernel_size: 5
    group: 2
    stride: 2
    stride: 1
    weight_filler {
      type: "xavier"
    }
    bias_filler {
      type: "xavier"
    }
    dilatio

In [23]:
mod.show()

## caffe crop

In [24]:
from caffe_utils import _test_op

def _test_crop(data, **kwargs):
    """One iteration of Crop"""
    _test_op(data, L.Crop, "Crop", **kwargs)


def test_forward_Crop():
    """Crop"""
    _test_crop([np.random.rand(10, 10, 120, 120), np.random.rand(10, 5, 50, 60)])
    _test_crop([np.random.rand(10, 10, 120, 120), np.random.rand(10, 5, 50, 60)], axis=1)
    _test_crop([np.random.rand(10, 10, 120, 120), np.random.rand(10, 5, 50, 60)], axis=1, offset=2)
    _test_crop(
        [np.random.rand(10, 10, 120, 120), np.random.rand(10, 5, 50, 60)], axis=1, offset=[1, 2, 4]
    )
    _test_crop(
        [np.random.rand(10, 10, 120, 120), np.random.rand(10, 5, 50, 60)], axis=2, offset=[2, 4]
    )
    _test_crop([np.random.rand(10, 120, 120), np.random.rand(5, 50, 60)], axis=1, offset=[2, 4])
    _test_crop([np.random.rand(120, 120), np.random.rand(50, 60)], axis=0, offset=[2, 4])

In [25]:
test_forward_Crop()

I0914 09:12:30.343927 1956768 solver.cpp:45] Initializing solver from parameters: 
train_net: "/home/ai/.tvm_test_data/caffe_test/Crop/Crop_10_10_120_120_10_5_50_60.prototxt"
base_lr: 0.01
display: 1
max_iter: 100000
lr_policy: "inv"
gamma: 0.0001
power: 0.75
momentum: 0.9
weight_decay: 0.0005
snapshot: 100000
snapshot_prefix: "/home/ai/.tvm_test_data/caffe_test/Crop/Crop_10_10_120_120_10_5_50_60"
I0914 09:12:30.344040 1956768 solver.cpp:92] Creating training net from train_net file: /home/ai/.tvm_test_data/caffe_test/Crop/Crop_10_10_120_120_10_5_50_60.prototxt
I0914 09:12:30.344126 1956768 net.cpp:53] Initializing net from parameters: 
state {
  phase: TRAIN
}
layer {
  name: "data0"
  type: "Input"
  top: "data0"
  input_param {
    shape {
      dim: 10
      dim: 10
      dim: 120
      dim: 120
    }
  }
}
layer {
  name: "data1"
  type: "Input"
  top: "data1"
  input_param {
    shape {
      dim: 10
      dim: 5
      dim: 50
      dim: 60
    }
  }
}
layer {
  name: "output"
  

## caffe Deconvolution

In [ ]:
def _test_deconvolution(data, **kwargs):
    """One iteration of Deconvolution"""
    _test_op(data, L.Deconvolution, "Deconvolution", **kwargs)


def test_forward_Deconvolution():
    """Deconvolution"""
    data = np.random.rand(1, 16, 32, 32).astype(np.float32)
    _test_deconvolution(
        data,
        convolution_param=dict(
            num_output=20,
            bias_term=True,
            pad=0,
            kernel_size=3,
            stride=2,
            dilation=1,
            weight_filler=dict(type="xavier"),
            bias_filler=dict(type="xavier"),
        ),
    )
    _test_deconvolution(
        data,
        convolution_param=dict(
            num_output=20,
            bias_term=False,
            pad=[1, 2],
            kernel_size=3,
            stride=2,
            dilation=1,
            weight_filler=dict(type="xavier"),
            bias_filler=dict(type="xavier"),
        ),
    )
    _test_deconvolution(
        data,
        convolution_param=dict(
            num_output=20,
            bias_term=True,
            pad_h=1,
            pad_w=2,
            kernel_h=3,
            kernel_w=5,
            stride_h=2,
            stride_w=1,
            dilation=1,
            weight_filler=dict(type="xavier"),
            bias_filler=dict(type="xavier"),
        ),
    )
    _test_deconvolution(
        data,
        convolution_param=dict(
            num_output=16,
            bias_term=False,
            pad=0,
            kernel_size=2,
            stride=2,
            dilation=1,
            group=16,
            weight_filler=dict(type="xavier"),
            bias_filler=dict(type="xavier"),
        ),
    )
    data = np.random.rand(1, 100, 32, 32).astype(np.float32)
    _test_deconvolution(
        data,
        convolution_param=dict(
            num_output=100,
            bias_term=False,
            pad=0,
            kernel_size=2,
            stride=2,
            dilation=1,
            group=100,
            weight_filler=dict(type="xavier"),
            bias_filler=dict(type="xavier"),
        ),
    )


## caffe Dropout

In [ ]:
def _test_dropout(data, **kwargs):
    """One iteration of Dropout"""
    _test_op(data, L.Dropout, "Dropout", **kwargs)


def test_forward_Dropout():
    """Dropout"""
    data = np.random.rand(1, 3, 10, 10).astype(np.float32)
    _test_dropout(data)
    _test_dropout(data, dropout_ratio=0.7)

## caffe Eltwise

In [ ]:
def _test_eltwise(data_list, **kwargs):
    """One iteration of Eltwise"""
    _test_op(data_list, L.Eltwise, "Eltwise", **kwargs)


def test_forward_Eltwise():
    """Eltwise"""
    _test_eltwise(
        [
            np.random.rand(1, 3, 10, 11).astype(np.float32),
            np.random.rand(1, 3, 10, 11).astype(np.float32),
        ],
        operation=0,
    )
    _test_eltwise(
        [
            np.random.rand(1, 3, 10, 11).astype(np.float32),
            np.random.rand(1, 3, 10, 11).astype(np.float32),
        ],
        operation=1,
    )
    _test_eltwise(
        [
            np.random.rand(1, 3, 10, 11).astype(np.float32),
            np.random.rand(1, 3, 10, 11).astype(np.float32),
        ],
        operation=2,
    )
    _test_eltwise(
        [
            np.random.rand(1, 3, 10, 11).astype(np.float32),
            np.random.rand(1, 3, 10, 11).astype(np.float32),
        ],
        operation=1,
        coeff=[0.5, 1],
    )
    _test_eltwise(
        [
            np.random.rand(1, 3, 10, 11).astype(np.float32),
            np.random.rand(1, 3, 10, 11).astype(np.float32),
            np.random.rand(1, 3, 10, 11).astype(np.float32),
        ],
        operation=0,
    )
    _test_eltwise(
        [
            np.random.rand(1, 3, 10, 11).astype(np.float32),
            np.random.rand(1, 3, 10, 11).astype(np.float32),
            np.random.rand(1, 3, 10, 11).astype(np.float32),
            np.random.rand(1, 3, 10, 11).astype(np.float32),
        ],
        operation=1,
    )
    _test_eltwise(
        [
            np.random.rand(1, 3, 10, 11).astype(np.float32),
            np.random.rand(1, 3, 10, 11).astype(np.float32),
            np.random.rand(1, 3, 10, 11).astype(np.float32),
            np.random.rand(1, 3, 10, 11).astype(np.float32),
            np.random.rand(1, 3, 10, 11).astype(np.float32),
        ],
        operation=2,
    )
    _test_eltwise(
        [
            np.random.rand(1, 3, 10, 11).astype(np.float32),
            np.random.rand(1, 3, 10, 11).astype(np.float32),
            np.random.rand(1, 3, 10, 11).astype(np.float32),
            np.random.rand(1, 3, 10, 11).astype(np.float32),
            np.random.rand(1, 3, 10, 11).astype(np.float32),
            np.random.rand(1, 3, 10, 11).astype(np.float32),
        ],
        operation=1,
        coeff=[0.5, 1, 0.2, 1.8, 3.1, 0.1],
    )


## caffe Flatten

In [ ]:
def _test_flatten(data, axis=1):
    """One iteration of Flatten"""
    _test_op(data, L.Flatten, "Flatten", axis=axis)


def test_forward_Flatten():
    """Flatten"""
    data = np.random.rand(1, 3, 10, 10).astype(np.float32)
    _test_flatten(data)
    _test_flatten(data, axis=1)

## caffe InnerProduct

In [ ]:
def _test_inner_product(data, **kwargs):
    """One iteration of InnerProduct"""
    _test_op(data, L.InnerProduct, "InnerProduct", **kwargs)


def test_forward_InnerProduct():
    """InnerProduct"""
    data = np.random.rand(1, 3, 10, 10)
    _test_inner_product(data, num_output=20, bias_term=False, weight_filler=dict(type="xavier"))
    _test_inner_product(
        data,
        num_output=20,
        bias_term=True,
        weight_filler=dict(type="xavier"),
        bias_filler=dict(type="xavier"),
    )
    _test_inner_product(
        np.random.rand(20, 10).astype(np.float32),
        num_output=30,
        bias_term=True,
        weight_filler=dict(type="xavier"),
        bias_filler=dict(type="xavier"),
    )


## caffe LRN

In [ ]:

def _test_lrn(data, local_size=5, alpha=1.0, beta=0.75, k=1.0):
    """One iteration of LRN"""
    _test_op(data, L.LRN, "LRN", local_size=local_size, alpha=alpha, beta=beta, k=k)


def test_forward_LRN():
    """LRN"""
    data = np.random.rand(1, 3, 10, 10).astype(np.float32)
    _test_lrn(data)
    _test_lrn(data, local_size=3)
    _test_lrn(data, local_size=3, alpha=2.0)
    _test_lrn(
        data,
        local_size=3,
        alpha=2.0,
        beta=0.5,
    )
    _test_lrn(data, local_size=3, alpha=2.0, beta=0.5, k=2.0)

## caffe Permute

In [ ]:

def _test_permute(data, **kwargs):
    """One iteration of Permute."""
    _test_op(data, L.Permute, "Permute", **kwargs)


def test_forward_Permute():
    """Permute"""
    data = np.random.rand(2, 3, 4).astype(np.float32)
    _test_permute(data, permute_param={"order": [0, 1, 2]})
    _test_permute(data, permute_param={"order": [0, 2, 1]})
    _test_permute(data, permute_param={"order": [1, 0, 2]})
    _test_permute(data, permute_param={"order": [1, 2, 0]})
    _test_permute(data, permute_param={"order": [2, 0, 1]})
    _test_permute(data, permute_param={"order": [2, 1, 0]})

## caffe Pooling

In [ ]:
def _test_pooling(data, **kwargs):
    """One iteration of Pooling."""
    _test_op(data, L.Pooling, "Pooling", **kwargs)


def test_forward_Pooling():
    """Pooing"""
    data = np.random.rand(1, 3, 10, 10).astype(np.float32)
    # MAX Pooling
    _test_pooling(data, kernel_size=2, stride=2, pad=0, pool=P.Pooling.MAX)
    _test_pooling(
        data, kernel_h=2, kernel_w=3, stride_h=2, stride_w=1, pad_h=1, pad_w=2, pool=P.Pooling.MAX
    )
    _test_pooling(data, pool=P.Pooling.MAX, global_pooling=True)

    # AVE Pooing
    _test_pooling(data, kernel_size=2, stride=2, pad=0, pool=P.Pooling.AVE)
    _test_pooling(
        data, kernel_h=2, kernel_w=3, stride_h=2, stride_w=1, pad_h=1, pad_w=2, pool=P.Pooling.AVE
    )
    _test_pooling(data, pool=P.Pooling.AVE, global_pooling=True)


## caffe Power

In [ ]:
def _test_power(data, **kwargs):
    """One iteration of Power."""
    _test_op(data, L.Power, "Power", **kwargs)


def test_forward_Power():
    """Power"""
    data = np.random.rand(1, 3, 10, 10).astype(np.float32)
    _test_power(data, power_param={"power": 0.37, "scale": 0.83, "shift": -2.4})
    _test_power(data, power_param={"power": 0.37, "scale": 0.83, "shift": 0.0})
    _test_power(data, power_param={"power": 0.0, "scale": 0.83, "shift": -2.4})
    _test_power(data, power_param={"power": 1.0, "scale": 0.83, "shift": -2.4})
    _test_power(data, power_param={"power": 2.0, "scale": 0.34, "shift": -2.4})
    _test_power(data, power_param={"power": 1.0, "scale": 1.0, "shift": 0.0})

## caffe PReLU

In [ ]:
def _test_prelu(data, **kwargs):
    """One iteration of PReLU."""
    _test_op(data, L.PReLU, "PReLU", **kwargs)


def test_forward_PReLU():
    """PReLU"""
    data = np.random.rand(1, 3, 10, 10).astype(np.float32)
    _test_prelu(data, filler=dict(type="constant", value=0.5))
    _test_prelu(data)
    _test_prelu(np.random.rand(10, 20).astype(np.float32))

## caffe ReLU

In [ ]:
def _test_relu(data, **kwargs):
    """One iteration of ReLU."""
    _test_op(data, L.ReLU, "ReLU", **kwargs)


def test_forward_ReLU():
    """ReLU"""
    data = np.random.rand(1, 3, 10, 10).astype(np.float32)
    _test_relu(data)
    _test_relu(np.random.rand(10, 20).astype(np.float32))

## caffe Reshape

In [ ]:
def _test_reshape(data, **kwargs):
    """One iteration of Reshape."""
    _test_op(data, L.Reshape, "Reshape", **kwargs)


def test_forward_Reshape():
    """Reshape"""
    data = np.random.rand(1, 8, 6).astype(np.float32)
    _test_reshape(data, reshape_param={"shape": {"dim": [4, 3, 4]}})
    _test_reshape(data, reshape_param={"shape": {"dim": [2, 0, 3]}})
    _test_reshape(data, reshape_param={"shape": {"dim": [2, 0, -1]}})
    _test_reshape(data, reshape_param={"shape": {"dim": [0, -1]}})

    _test_reshape(data, reshape_param={"shape": {"dim": [2, 3]}, "axis": 2})
    _test_reshape(data, reshape_param={"shape": {"dim": [4, 3, 4]}, "axis": 1})
    _test_reshape(data, reshape_param={"shape": {"dim": [4, 3, 4]}, "axis": -3})

    _test_reshape(data, reshape_param={"shape": {"dim": [2, 4]}, "axis": 1, "num_axes": 1})
    _test_reshape(data, reshape_param={"shape": {"dim": [3, 16]}, "axis": 1, "num_axes": 2})


## caffe Scale

In [ ]:
def _test_scale(data, **kwargs):
    """One iteration of Scale."""
    _test_op(data, L.Scale, "Scale", **kwargs)


def test_forward_Scale():
    """Scale"""
    data = np.random.rand(1, 3, 10, 10).astype(np.float32)
    _test_scale(data, filler=dict(type="xavier"))
    _test_scale(data, filler=dict(type="xavier"), bias_term=True, bias_filler=dict(type="xavier"))

## caffe Sigmoid

In [ ]:
def _test_sigmoid(data, **kwargs):
    """One iteration of Sigmoid."""
    _test_op(data, L.Sigmoid, "Sigmoid", **kwargs)


def test_forward_Sigmoid():
    """Sigmoid"""
    data = np.random.rand(1, 3, 10, 10).astype(np.float32)
    _test_sigmoid(data)

## caffe Slice

In [ ]:
def _test_slice(data, **kwargs):
    """One iteration of Slice"""
    _test_op(data, L.Slice, "Slice", **kwargs)


def test_forward_Slice():
    """Slice"""
    data = np.random.rand(1, 3, 10, 10).astype(np.float32)
    _test_slice(data, ntop=2, slice_param=dict(axis=1, slice_point=[1]))
    _test_slice(data, ntop=2, slice_param=dict(axis=-1, slice_point=[1]))
    _test_slice(data, ntop=3, slice_param=dict(axis=2, slice_point=[1, 6]))
    _test_slice(data, ntop=3)

## caffe Softmax

In [ ]:
def _test_softmax(data, **kwargs):
    """One iteration of Softmax"""
    _test_op(data, L.Softmax, "Softmax", **kwargs)


def test_forward_Softmax():
    """Softmax"""
    _test_softmax(np.random.rand(1, 3, 10, 10).astype(np.float32))
    _test_softmax(np.random.rand(1, 3, 10, 10).astype(np.float32), axis=2)
    _test_softmax(np.random.rand(10, 10).astype(np.float32), axis=0)
    _test_softmax(np.random.rand(2, 10, 10).astype(np.float32), axis=1)


## caffe TanH

In [ ]:
def _test_tanh(data, **kwargs):
    """One iteration of TanH"""
    _test_op(data, L.TanH, "TanH", **kwargs)


def test_forward_TanH():
    """TanH"""
    _test_tanh(np.random.rand(1, 3, 10, 10).astype(np.float32))
    _test_tanh(np.random.rand(3, 10, 10).astype(np.float32))
    _test_tanh(np.random.rand(10, 10).astype(np.float32))
    _test_tanh(np.random.rand(10).astype(np.float32))

## caffe Reduction 

In [ ]:

def _test_reduction(data, **kwargs):
    """One iteration of Reduction"""
    _test_op(data, L.Reduction, "Reduction", **kwargs)


def test_forward_Reduction():
    """Reduction"""
    reduction_op = {"SUM": 1, "ASUM": 2, "SUMSQ": 3, "MEAN": 4}
    _test_reduction(np.random.rand(10).astype(np.float32), operation=reduction_op["SUM"], axis=0)
    _test_reduction(
        np.random.rand(10, 20, 30, 40).astype(np.float32), operation=reduction_op["SUM"], axis=3
    )
    _test_reduction(
        np.random.rand(10, 20, 30, 40).astype(np.float32), operation=reduction_op["SUM"], axis=1
    )
    _test_reduction(
        np.random.rand(10).astype(np.float32), operation=reduction_op["SUM"], axis=0, coeff=0.5
    )
    _test_reduction(
        np.random.rand(10, 20, 30, 40).astype(np.float32),
        operation=reduction_op["SUM"],
        axis=3,
        coeff=5.0,
    )
    _test_reduction(np.random.rand(10).astype(np.float32), operation=reduction_op["ASUM"])
    _test_reduction(
        np.random.rand(10, 20).astype(np.float32), operation=reduction_op["ASUM"], axis=1
    )
    _test_reduction(
        np.random.rand(10, 20, 30, 40).astype(np.float32), operation=reduction_op["ASUM"], axis=3
    )
    _test_reduction(
        np.random.rand(10).astype(np.float32), operation=reduction_op["ASUM"], axis=0, coeff=0.0
    )
    _test_reduction(
        np.random.rand(10, 20, 30).astype(np.float32),
        operation=reduction_op["ASUM"],
        axis=2,
        coeff=7.0,
    )
    _test_reduction(
        np.random.rand(10, 20, 30, 40, 10).astype(np.float32),
        operation=reduction_op["ASUM"],
        axis=3,
        coeff=1.0,
    )
    _test_reduction(np.random.rand(10).astype(np.float32), operation=reduction_op["SUMSQ"], axis=0)
    _test_reduction(
        np.random.rand(10, 20, 30, 40).astype(np.float32), operation=reduction_op["SUMSQ"], axis=3
    )
    _test_reduction(
        np.random.rand(10).astype(np.float32), operation=reduction_op["SUMSQ"], axis=0, coeff=0.0
    )
    _test_reduction(
        np.random.rand(10, 20, 30, 40, 50).astype(np.float32),
        operation=reduction_op["SUMSQ"],
        axis=4,
        coeff=2.0,
    )
    _test_reduction(np.random.rand(10).astype(np.float32), operation=reduction_op["MEAN"], axis=0)
    _test_reduction(
        np.random.rand(10, 20, 30, 40).astype(np.float32), operation=reduction_op["MEAN"], axis=3
    )
    _test_reduction(
        np.random.rand(10).astype(np.float32), operation=reduction_op["MEAN"], axis=0, coeff=0.0
    )
    _test_reduction(
        np.random.rand(10, 20, 30, 40).astype(np.float32),
        operation=reduction_op["MEAN"],
        axis=3,
        coeff=2.0,
    )


## caffe Embed

In [ ]:
def _test_embed(data, **kwargs):
    """One iteration of Embed"""
    _test_op(data, L.Embed, "Embed", **kwargs)


def test_forward_Embed():
    """Embed"""
    k = 20
    data = list(i for i in range(k))
    np.random.shuffle(data)
    # dimension is 1
    data = np.asarray(data)
    _test_embed(
        data,
        num_output=30,
        input_dim=k,
        bias_term=True,
        weight_filler=dict(type="xavier"),
        bias_filler=dict(type="xavier"),
    )
    _test_embed(
        data,
        num_output=30,
        input_dim=k,
        bias_term=False,
        weight_filler=dict(type="xavier"),
        bias_filler=dict(type="xavier"),
    )
    # dimension is 2
    data = np.reshape(data, [4, 5])
    _test_embed(
        data,
        num_output=30,
        input_dim=k,
        bias_term=True,
        weight_filler=dict(type="xavier"),
        bias_filler=dict(type="xavier"),
    )
    _test_embed(
        data,
        num_output=30,
        input_dim=k,
        bias_term=False,
        weight_filler=dict(type="xavier"),
        bias_filler=dict(type="xavier"),
    )
    # dimension is 3
    data = np.reshape(data, [2, 2, 5])
    _test_embed(
        data,
        num_output=30,
        input_dim=k,
        bias_term=True,
        weight_filler=dict(type="xavier"),
        bias_filler=dict(type="xavier"),
    )
    _test_embed(
        data,
        num_output=30,
        input_dim=k,
        bias_term=False,
        weight_filler=dict(type="xavier"),
        bias_filler=dict(type="xavier"),
    )
    # dimension is 4
    data = np.reshape(data, [2, 2, 5, 1])
    _test_embed(
        data,
        num_output=30,
        input_dim=k,
        bias_term=True,
        weight_filler=dict(type="xavier"),
        bias_filler=dict(type="xavier"),
    )
    _test_embed(
        data,
        num_output=30,
        input_dim=k,
        bias_term=False,
        weight_filler=dict(type="xavier"),
        bias_filler=dict(type="xavier"),
    )

